In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pandas as pd
import numpy as np
import pickle
import sys
import time
import glob
import re
from tqdm.notebook import trange, tqdm
import classifier_utils as cu
import utils
import plotly.figure_factory as ff
from plotly.subplots import make_subplots

from plotly.offline import init_notebook_mode
import plotly.offline as py
import plotly.graph_objs as go
init_notebook_mode(connected=True)

In [238]:
# blockbot_user_tweets = utils.load_user_tweets('../data/BBlevel1_user_tweets', min_tweets=500, limit=500)
# control_user_tweets = utils.load_user_tweets('../data/control_user_tweets2/', min_tweets=500, limit=500)
# naziblkr_user_tweets = utils.load_user_tweets('../data/NaziBlocker_user_tweets/', min_tweets=500, limit=500)
ggautoblkr_user_tweets = utils.load_user_tweets('../data/ggautoblocker_user_tweets/', min_tweets=500, limit=500)

In [239]:
len(ggautoblkr_user_tweets)

501

In [241]:
user_lists = [
    ('blockbot', blockbot_user_tweets),
    ('naziblkr', naziblkr_user_tweets),
    ('ggautoblockr', ggautoblkr_user_tweets),
    ('control2', control_user_tweets)
]

In [3]:
user_list_names = ['blockbot', 'naziblkr', 'ggautoblockr', 'control2']

In [163]:

model_files = [
    'final_model_toxic_comments_identity_hate.p',
    'final_model_toxic_comments_insult.p',
    'final_model_toxic_comments_obscene.p',
    'final_model_toxic_comments_severe_toxic.p',
    'final_model_toxic_comments_threat.p',
    'final_model_toxic_comments_toxic.p',
    
    'final_model_gboost_toxic_comments_identity_hate.p',
    'final_model_gboost_toxic_comments_insult.p',
    'final_model_gboost_toxic_comments_obscene.p',
    'final_model_gboost_toxic_comments_severe_toxic.p',
    'final_model_gboost_toxic_comments_threat.p',
    'final_model_gboost_toxic_comments_toxic.p',
    
    'final_model_gboost_hate_offensive_Hate.p',
    'final_model_gboost_hate_offensive_Offensive.p',
    'final_model_gboost_hate_abuse_abusive.p',
    'final_model_gboost_hate_abuse_hateful.p',
]
models = []
for file in model_files:
    with open(file, 'rb') as f:
        models.append((file, pickle.load(f)))

In [154]:
def predict_list(user_tweets, model):
    user_scores = {}
    user_preds = {}
    for uid, tweets in tqdm(user_tweets.items()):
        probs = model.predict_proba(tweets)[:, 1]
        user_scores[uid] = probs.mean(axis=0)
        user_preds[uid] = probs
    return user_scores, user_preds


        

In [12]:
def compute_harassment_frac(user_tweets, threshold=0.5):
    user_scores = {}
    for uid, tweet_probs in user_tweets.items():
        user_scores[uid] = (tweet_probs > threshold).sum() / len(tweet_probs)
    return user_scores

In [136]:
fig = go.Figure()
fig.add_trace(
    go.Histogram(x=list(compute_harassment_frac(results['final_model_gboost_toxic_comments_toxic.p']['blockbot'][1]).values()))
)

fig.add_trace(
    go.Histogram(x=list(compute_harassment_frac(results['final_model_gboost_toxic_comments_toxic.p']['control'][1]).values()))
)

fig.show()

In [4]:
with open('predict_blocklists_res2.p', 'rb') as f:
    results = pickle.load(f)

In [243]:
# results = {}
for name, m in models:
    if name in results:
        model_res = results[name]
    else:
        model_res = {}
    for list_name, user_tweets in user_lists:
        if list_name in model_res:
            continue
        print('Model: ', name, 'List', list_name)
        model_res[list_name] = predict_list(user_tweets, m)
    results[name] = model_res

Model:  final_model_toxic_comments_identity_hate.p List ggautoblockr


/usr/local/lib/python3.6/dist-packages/sklearn/feature_extraction/text.py:385: UserWarning:

Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'", 'becau'] not in stop_words.




Model:  final_model_toxic_comments_insult.p List ggautoblockr



Model:  final_model_toxic_comments_obscene.p List ggautoblockr



Model:  final_model_toxic_comments_severe_toxic.p List ggautoblockr


...


Model:  final_model_gboost_toxic_comments_toxic.p List ggautoblockr



Model:  final_model_gboost_hate_offensive_Hate.p List ggautoblockr



Model:  final_model_gboost_hate_offensive_Offensive.p List ggautoblockr



Model:  final_model_gboost_hate_abuse_abusive.p List ggautoblockr



Model:  final_model_gboost_hate_abuse_hateful.p List ggautoblockr


In [ ]:
# results = {}
for name, m in models:
    model_res = {}
    for list_name, user_tweets in user_lists:
        print('Model: ', name, 'List', list_name)
        model_res[list_name] = predict_list(user_tweets, m)
    results[name] = model_res


Model:  final_model_gboost_toxic_comments_identity_hate.p List blockbot


In [244]:
with open('predict_blocklists_res2.p', 'wb') as f:
    pickle.dump(results, f)

In [161]:
results.keys()

dict_keys(['final_model_toxic_comments_identity_hate.p', 'final_model_toxic_comments_insult.p', 'final_model_toxic_comments_obscene.p', 'final_model_toxic_comments_severe_toxic.p', 'final_model_toxic_comments_threat.p', 'final_model_toxic_comments_toxic.p', 'final_model_gboost_toxic_comments_identity_hate.p', 'final_model_gboost_toxic_comments_insult.p', 'final_model_gboost_toxic_comments_obscene.p', 'final_model_gboost_toxic_comments_severe_toxic.p', 'final_model_gboost_toxic_comments_threat.p', 'final_model_gboost_toxic_comments_toxic.p'])

In [9]:
model_names = [
    'final_model_gboost_toxic_comments_toxic.p',
    'final_model_gboost_toxic_comments_obscene.p',
    'final_model_gboost_toxic_comments_insult.p',

    
    'final_model_gboost_hate_abuse_abusive.p',
    'final_model_gboost_hate_abuse_hateful.p',
    
    'final_model_gboost_hate_offensive_Offensive.p',
    'final_model_gboost_hate_offensive_Hate.p',
]

display_names = [
    '$D_1 \\text{: Toxic}$',
#     '$D_1 \\text{: Severe Toxic}$',
    '$D_1 \\text{: Obscene}$',
#     '$D_1 \\text{: Threat}$',
    '$D_1 \\text{: Insult}$',
#     '$D_1 \\text{: Identity Hate}$',
    
    
    '$D_2 \\text{: Abusive}$',
    '$D_2 \\text{: Hateful}$',
    
    '$D_3 \\text{: Offensive}$',
    '$D_3 \\text{: Hate}$',
    
]

list_display_names = ['BlockBot', 'NaziBlocker', 'GGAutoBlocker', 'Random']

colors = [
    '#1f77b4',  # muted blue
    '#ff7f0e',  # safety orange
    '#2ca02c',  # cooked asparagus green
#     '#d62728',  # brick red
    '#9467bd',  # muted purple
    '#8c564b',  # chestnut brown
    '#e377c2',  # raspberry yogurt pink
    '#7f7f7f',  # middle gray
    '#bcbd22',  # curry yellow-green
    '#17becf'   # blue-teal
]

In [11]:

fig = make_subplots(rows=4, cols=2, subplot_titles=display_names)
fig.update_layout(
    autosize=False,
    width=500,
    height=500,
    legend=dict(x=0.6, y=0),
    margin=dict(l=20, r=20, t=20, b=20)
)
showlegend=True
c = 0
for model_name in model_names:
    res = results[model_name]
    for i in range(len(user_list_names)):
        list_name = user_list_names[i]
        user_scores = list(res[list_name][0].values())
        bin_edges = np.histogram_bin_edges(user_scores, bins='auto', range=(0.0, 0.5))
        
        weights = np.ones_like(user_scores)/(len(user_scores))
        hist, _= np.histogram(user_scores, bins=bin_edges, weights=weights)
        fig.add_trace(
            go.Scatter(
                x=bin_edges, y=hist, 
                name=list_display_names[i],
                mode='lines', 
                legendgroup="group", 
                showlegend=showlegend,
                line=dict(color=colors[i]),
            ),
            col= c % 2 + 1, row= c // 2 + 1
        )
    c += 1
    showlegend=False
fig.show()

In [21]:

fig = make_subplots(rows=4, cols=2, subplot_titles=display_names)
fig.update_layout(
    autosize=False,
    width=500,
    height=500,
    legend=dict(x=0.6, y=0),
    margin=dict(l=20, r=20, t=20, b=20)
)
showlegend=True
c = 0
for model_name in model_names:
    res = results[model_name]
    for i in range(len(user_list_names)):
        list_name = user_list_names[i]
        user_scores = list(compute_harassment_frac(res[list_name][1]).values())
        
        bin_edges = np.histogram_bin_edges(user_scores, bins='auto', range=(0.0, 0.25))
        
        weights = np.ones_like(user_scores)/(len(user_scores))
        hist, _= np.histogram(user_scores, bins=bin_edges, weights=weights)
        fig.add_trace(
            go.Scatter(
                x=bin_edges, y=hist, 
                name=list_display_names[i],
                mode='lines', 
                legendgroup="group", 
                showlegend=showlegend,
                line=dict(color=colors[i], shape='hvh')
            ),
#             go.Histogram(
#                 x=user_scores, 
#                 histnorm='probability',
#                 legendgroup="group", 
#                 showlegend=showlegend,
#             ),
            col= c % 2 + 1, row= c // 2 + 1
        )
    c += 1
    showlegend=False
    
fig.update_layout(barmode='overlay')
# fig.update_traces(opacity=0.25)
fig.show()

In [201]:
selected_models = [
#     'final_model_gboost_toxic_comments_identity_hate.p',
#     'final_model_gboost_toxic_comments_insult.p',
#     'final_model_gboost_toxic_comments_obscene.p',
#     'final_model_gboost_toxic_comments_severe_toxic.p',
#     'final_model_gboost_toxic_comments_threat.p',
#     'final_model_gboost_toxic_comments_toxic.p',
    
    'final_model_gboost_hate_offensive_Hate.p',
    'final_model_gboost_hate_offensive_Offensive.p',
    'final_model_gboost_hate_abuse_abusive.p',
    'final_model_gboost_hate_abuse_hateful.p',
]
fig = make_subplots(rows=2, cols=3, subplot_titles=selected_models)

c = 0
for model_name in selected_models:
    res = results[model_name]
    for list_name in user_list_names:
        user_scores = list(compute_harassment_frac(res[list_name][1], threshold=0.5).values())
        bin_edges = np.histogram_bin_edges(user_scores, bins='auto', range=(0.0, 0.2))
        hist, _= np.histogram(user_scores, bins=bin_edges, density=True)
#         print(c % 3 + 1, c // 3 + 1)
        fig.add_trace(
            go.Scatter(x=bin_edges, y=hist, name=list_name),
            col= c % 3 + 1, row= c // 3 + 1
        )
    c += 1
fig.show()

In [233]:
user_scores, user_preds = results['final_model_gboost_hate_abuse_abusive.p']['control2']

In [234]:
tweets = np.array(control_user_tweets[1343248716])
preds = user_preds[1343248716]

In [236]:
tweets[preds > 0.6]

array(['I’m cool off a lot of ppl and a lot of shit. I ain’t gonna keep giving ppl chances.',
       'I’m not playing these games with ppl nomore. Fuck you.',
       'I’m chillin on the soft ass bed in my job. I’m not goin back til like 8:30',
       'You’re really for the socials. When I catch you ima fuck u up for ducking me. 😒 https://t.co/g3q9D0Og9T',
       'I’m mad ashit. I should’ve never came in this mf.',
       '@_maine3200 Rs like what? Pussy why tf u sittin like that? 😭😭😂 he deserves to get smacked',
       'Dumb ass 😭😭😭😭😍😍 https://t.co/6zGE4V7jj7',
       'This me 😭😭😭😭 I don’t be feeling like that shit https://t.co/Y8TK6xiEZv',
       'Dickeater. Shit ain’t cute.',
       'This is the one yo. Bitches be slizz yo https://t.co/KqESbCI1Ap',
       'The ass eataaaas is up I see',
       'I keep losing my damn blistex. This is so annoying.',
       'I been in the crib on bummy shit all day. I need at least 5 days out the month to do this. 😭',
       'I want a sturdy ass tat on 

In [204]:
user_fracs = compute_harassment_frac(user_preds, threshold=0.6)

In [206]:
[uid for uid, f in user_fracs.items() if f > 0.1]

[3074250784,
 1014607448,
 1343248716,
 620357368,
 329528053,
 314255921,
 229740374,
 883271695808827393,
 759950272865206272,
 231245191,
 2771591368,
 3832455134,
 70309818,
 464282652,
 1123440014547922946,
 2654608408,
 3754735692]

In [26]:

for uid, tweets in control_user_tweets.items():
    probs = model.predict_proba(tweets)[:, 1]
    print(uid)
    print(np.array(tweets)[probs > 0.8])

996438129014800384
[]
17410741
[]
831815773
[]
1100900948493373440
['@HtsAdrien What the fuck']
1177062833433059328
[]
3077435434
[]
467134773
["vegans be like: what the fuck is a carbon emission bitch I'm gonna kill you"
 'nerve pain fucking sucks'
 '@meowtorcycle the fuck who does that shit thats fucked'
 'Oh shit oh fuck https://t.co/WvPJhIpRsU' '@furry_yuri what the fuck'
 'WHAT THE FUCK WAS NO ONE GONNA TELL ME https://t.co/VC16r1lzMK'
 '@real__slick get fucked leon' '@neiltyson shut up rapist']
292557320
['@susanas4321 That sucks Susan.  😢']
732642506
['@ChallisCorinna Ps go fuck yourself.'
 '@matthew_land Chips you fucking freak' '@MatthewLand5 Fuck off'
 '@ChallisCorinna Suck my dick'
 'Fucking hate miserable customers, fuck off Shirley you rude slut.'
 'What a fucking shit day😛' '@ChallisCorinna Fuck off get out'
 'What a fucking cunt.' 'What a fucking shit night😫😰😓'
 '@heals_shannon u fuck x' '@ChallisCorinna fuck off x'
 "@Abiselby 'fucking bitch'" '@ChallisCorinna where the

[]
220963243
[]
962043808106991617
[]
1066744886421069825
[]
2235844939
['what the fuck https://t.co/pJdAkyR8w2' '@ikemenkuro mom holy fuck'
 'I HATE YOU BETHESDA GO FUCK YOURSELF TODD HOWARD'
 'I FUCKING HATE YOU TODD HOWARD' 'I fucking HATE you b*thesda'
 '@pinnateleif ughhhhhhhhhhh I was so fucking mad . stupid ass.'
 '@plcntagenet FUCK THATS SO FUCKING UPSETTING FINAL FANTASY WHAT ARE U DOING!!!!! SQUARE WHAT ARE U DOING'
 "riot games can fucking fight me and I'd still win . pussy ass bitch"
 'origin are u gonna stop being a little bitch' '@dovetailx_x holy fuck']
420279575
[]
857117347
['@rjochoa Ohhhhhh they Bitch Bitch' 'NEVA LET HOE ASS NIGGAZ RIIDEEEE'
 'You gon Fuck around and drown off this🌊' 'What a Boring ass Sunday'
 'Fuck you Josh Brolin!!!'
 "If you don't fucks with us we will Bomb yo ass!! The US are back to being some Gangstas👏"
 'Fuck that ima take a shower.' 'Trump has a shrimp dick'
 '@RealSkipBayless Go fuck a 🐐' 'Fuck OU']
28800297
[]
526860979
["@PaladinAmber @s

ValueError: Found array with 0 sample(s) (shape=(0, 20000)) while a minimum of 1 is required.

In [18]:
blockbot_user_scores = {}
for uid, tweets in tqdm(blockbot_user_tweets.items()):
    if len(tweets) < 500 or uid in blockbot_user_scores:
        continue
    probs = model.predict_proba(tweets)
    blockbot_user_scores[uid] = probs.mean(axis=0)
    if len(blockbot_user_scores) >= 500:
        break
        
        
control_user_scores = {}
for uid, tweets in tqdm(control_user_tweets.items()):
    if len(tweets) < 500 or uid in control_user_scores:
        continue
    probs = model.predict_proba(tweets)
    control_user_scores[uid] = probs.mean(axis=0)
    if len(control_user_scores) >= 500:
        break
        
        
naziblkr_user_scores = {}
for uid, tweets in tqdm(naziblkr_user_tweets.items()):
    if len(tweets) < 500 or uid in naziblkr_user_scores:
        continue
    probs = model.predict_proba(tweets)
    naziblkr_user_scores[uid] = probs.mean(axis=0)
    if len(naziblkr_user_scores) >= 500:
        break

In [29]:
len(nazi_bot_x)

693

In [20]:
block_bot_x=[v[1] for v in control_user_scores.values()]
nazi_bot_x=[v[1] for v in naziblkr_user_scores.values()]
control_x=[v[1] for v in blockbot_user_scores.values()]
fig = ff.create_distplot([block_bot_x, nazi_bot_x, control_x], ['BlockBot', 'NaziBlkr',  'Control'], bin_size=.005)
fig.show()

In [15]:
len(control_user_scores), len(blockbot_user_scores)

(359, 0)

In [14]:
blockbot_user_scores = {}
for uid, tweets in tqdm(blockbot_user_tweets.items()):
    if len(tweets) < 500 or uid in blockbot_user_scores:
        continue
    probs = model.predict_proba(tweets)
    blockbot_user_scores[uid] = [probs[i][:, 1].mean() for i in range(len(classes))]
    if len(blockbot_user_scores) >= 1000:
        break

KeyboardInterrupt: 

In [ ]:
control_user_scores = {}
for uid, tweets in tqdm(control_user_tweets.items()):
    if len(tweets) < 500 or uid in control_user_scores:
        continue
    probs = model.predict_proba(tweets)
    control_user_scores[uid] = [probs[i][:, 1].mean() for i in range(len(classes))]
    if len(control_user_scores) >= 1000:
        break

In [ ]:
with open('user_scores_blobkbot_control_model_toxic_comments.p', 'wb') as f:
    pickle.dump((control_user_scores, blockbot_user_scores), f)

In [70]:
with open('user_scores_blobkbot_control_model_hate_abuse.p', 'wb') as f:
    pickle.dump((control_user_scores, blockbot_user_scores), f)

In [77]:
with open('user_scores_blobkbot_control_model_hate_offensive_speech.p', 'wb') as f:
    pickle.dump((control_user_scores, blockbot_user_scores), f)

In [90]:
with open('user_scores_blobkbot_control_model_harassment_umd.p', 'wb') as f:
    pickle.dump((control_user_scores, blockbot_user_scores), f)

In [9]:


for i in range(len(classes)):
    print(classes[i])
    block_bot_x=[v[i] for v in control_user_scores.values()]
    control_x=[v[i] for v in blockbot_user_scores.values()]
    fig = ff.create_distplot([block_bot_x, control_x], ['BlockBot', 'Control'], bin_size=.01)
    fig.show()


a


b


u


IndexError: index 2 is out of bounds for axis 0 with size 2

In [78]:


for i in range(len(classes)):
    print(classes[i])
    block_bot_x=[v[i] for v in control_user_scores.values()]
    control_x=[v[i] for v in blockbot_user_scores.values()]
    fig = ff.create_distplot([block_bot_x, control_x], ['BlockBot', 'Control'], bin_size=.01)
    fig.show()


hate


offensive


neither


In [71]:


for i in range(len(classes)):
    print(classes[i])
    block_bot_x=[v[i] for v in control_user_scores.values()]
    control_x=[v[i] for v in blockbot_user_scores.values()]
    fig = ff.create_distplot([block_bot_x, control_x], ['BlockBot', 'Control'], bin_size=.01)
    fig.show()


abusive


hateful


normal


spam


In [59]:


for i in range(len(classes)):
    print(classes[i])
    block_bot_x=[v[i] for v in control_user_scores.values()]
    control_x=[v[i] for v in blockbot_user_scores.values()]
    fig = ff.create_distplot([block_bot_x, control_x], ['BlockBot', 'Control'], bin_size=.01)
    fig.show()


toxic


severe_toxic


obscene


threat


insult


identity_hate


In [47]:
len(control_user_scores), len(blockbot_user_scores)

(359, 793)